# 터미널, 관광지, 누비자 이동경로 시각화

## 1. 데이터 불러오기

In [3]:
import pandas as pd
import folium
from folium.plugins import MarkerCluster
from haversine import haversine

In [4]:
df_merge = pd.read_csv('data/데이터병합.csv', sep=',', encoding='cp949')
df_merge.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 283 entries, 0 to 282
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   터미널명    283 non-null    object 
 1   주소      282 non-null    object 
 2   등록일자    282 non-null    object 
 3   위도      282 non-null    float64
 4   경도      282 non-null    float64
 5   번호      283 non-null    int64  
 6   보관대수    283 non-null    int64  
dtypes: float64(2), int64(2), object(3)
memory usage: 15.6+ KB


In [5]:
df_attraction = pd.read_csv('data/경상남도_창원시_주요관광지점 입장객_220627_워도.경도 ver.csv', sep=',', encoding='cp949')
df_attraction.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 28 entries, 0 to 27
Data columns (total 11 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   관광지             27 non-null     object 
 1   합계              23 non-null     object 
 2   2022년 01월(내국인)  23 non-null     object 
 3   2022년 01월(외국인)  23 non-null     float64
 4   2022년 02월(내국인)  23 non-null     object 
 5   2022년 02월(외국인)  23 non-null     float64
 6   2022년 03월(내국인)  23 non-null     object 
 7   2022년 03월(외국인)  23 non-null     float64
 8   위도              26 non-null     float64
 9   경도              26 non-null     float64
 10  Unnamed: 10     27 non-null     object 
dtypes: float64(5), object(6)
memory usage: 2.5+ KB


In [6]:
for i in range(3, 13):
    globals()['df_path{}'.format(i)] = pd.read_excel('data/path/path_count{}.xlsx'.format(i), engine='openpyxl')

## 2. 시각화함수

In [7]:
def MapEDA(df_merge, df_attraction, df_path):
    df_path = df_path[df_path['개수']>=500]
    df_merge = df_merge.dropna(axis=0)
    df_attraction = df_attraction.dropna(axis=0)


    m = folium.Map(
        location=[35.2538, 128.6402],
        zoom_start=11
    )

    coords1 = df_merge[['번호','위도', '경도']]
    coords2 = df_attraction[['관광지','위도', '경도']]

    marker_cluster1 = MarkerCluster().add_to(m)

    marker_cluster2 = MarkerCluster().add_to(m)

    for name, lat, long in zip(coords2['관광지'], coords2['위도'], coords2['경도']):
        folium.Marker([lat, long], tooltip= name, icon = folium.Icon(icon ="star", color="red")).add_to(marker_cluster2)
        
    
    extract_col = df_merge[['번호', '위도', '경도']]
    terminal_dict = dict()
    
    for num, lat, long in zip(extract_col['번호'], extract_col['위도'], extract_col['경도']):
        terminal_dict[num] = [lat, long]
    
    samePath = []
    for path in df_path['경로']:
        sp_lst = path.split('~')
        if sp_lst[0] == sp_lst[1]:
            samePath.append(int(sp_lst[0]))
            

    searchNode_dict = dict()
    for stdnum in samePath:
        distance = 100000
        for terminal_num in list(terminal_dict.keys()):
            # print(terminal_num)
            if terminal_num == stdnum:
                continue
            node1 = terminal_dict[stdnum]
            node2 = terminal_dict[terminal_num]
            dist = haversine(node1, node2)
            # dist = math.sqrt(pow(node1[0] - node2[0],2) + pow(node1[1] - node2[1],2))
            if dist < distance:
                distance = dist
                result = [stdnum, terminal_num, distance]
        searchNode_dict[result[0]] = distance
    
    marker_cluster3 = MarkerCluster().add_to(m)

    for name, lat, long in zip(coords1['번호'], coords1['위도'], coords1['경도']):
        folium.Marker([lat, long], popup= name, icon = folium.Icon(color="green")).add_to(marker_cluster1)
        if name in samePath:
            folium.Circle([lat, long], radius = searchNode_dict[name] * 800).add_to(m)
    
    diffPath = []
    for path, count in zip(df_path['경로'], df_path['개수']):
        if count >= 1100:
            weight = 8
        elif count >= 900:
            weight = 6
        elif count >= 700:
            weight = 4
        else:
            weight = 2

        sp_lst = path.split('~')
        if sp_lst[0] != sp_lst[1]:
                diffPath.append([int(sp_lst[0]), int(sp_lst[1]), weight])
    
    for depart_num, arrive_num, weight in diffPath:
        folium.PolyLine(
            locations = [terminal_dict[depart_num],terminal_dict[arrive_num]],
            tooltip = '{}->{}, 가중치: {}'.format(depart_num, arrive_num, weight),
            weight= weight
        ).add_to(m)
    return m

### 3월 시각화

In [8]:
map3 = MapEDA(df_merge, df_attraction, df_path3)
map3

### 4월 시각화

In [9]:
map4 = MapEDA(df_merge,  df_attraction , df_path4)
map4

### 5월 시각화

In [10]:
map5 = MapEDA(df_merge,  df_attraction , df_path5)
map5

### 6월 시각화

In [11]:
map6 = MapEDA(df_merge,  df_attraction , df_path6)
map6

### 7월 시각화

In [12]:
map7 = MapEDA(df_merge,  df_attraction , df_path7)
map7

### 8월 시각화

In [13]:
map8 = MapEDA(df_merge,  df_attraction , df_path8)
map8

### 9월 시각화

In [14]:
map9 = MapEDA(df_merge,  df_attraction , df_path9)
map9

### 10월 시각화

In [15]:
map10 = MapEDA(df_merge,  df_attraction , df_path10)
map10

### 11월 시각화

In [16]:
map11 = MapEDA(df_merge,  df_attraction , df_path11)
map11

### 12월 시각화

In [17]:
map12 = MapEDA(df_merge,  df_attraction , df_path12)
map12